In [1]:
import numpy as np
import pandas as pd
import re,os
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
import kagglehub

# Download latest version
path = kagglehub.dataset_download("lakshmi25npathi/imdb-dataset-of-50k-movie-reviews")

print("Path to dataset files:", path)

100%|██████████| 25.7M/25.7M [00:02<00:00, 12.1MB/s]

Extracting files...


Path to dataset files: /root/.cache/kagglehub/datasets/lakshmi25npathi/imdb-dataset-of-50k-movie-reviews/versions/1


In [3]:
datasets = path

file_name = os.listdir(datasets)
print(file_name)

data = os.path.join(datasets,'IMDB Dataset.csv')

['IMDB Dataset.csv']


In [33]:
df = pd.read_csv(data)

In [34]:
df.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [13]:
import nltk
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.corpus import wordnet
nltk.download('punkt')
nltk.download('punkt_tab')
nltk.download('stopwords')
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer,PorterStemmer

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [14]:
stopwords.words('english')[:4]

['a', 'about', 'above', 'after']

In [15]:
word_tokenize('hii my name is bantee')

['hii', 'my', 'name', 'is', 'bantee']

In [17]:
lem = WordNetLemmatizer()
text = 'i am coming'
text = word_tokenize(text)
print(text)
w = [lem.lemmatize(i,wordnet.VERB) for i in text]
print(w)

['i', 'am', 'coming']
['i', 'be', 'come']


In [18]:
stem = PorterStemmer()
text = 'he is changing bulb'
text = word_tokenize(text)
print(text)

w = [stem.stem(i,wordnet.VERB) for i in text]
print(w)



['he', 'is', 'changing', 'bulb']
['he', 'is', 'chang', 'bulb']


In [30]:
def clean_sent(text):
  text = re.sub(r'@\w+', '', text)  # Remove @mentions
  text = re.sub(r'http\S+|www\S+', '', text)# Remove URLs
  text = re.sub(r'<.*?>', '', text)  # Remove HTML tags
  text = re.sub(r'[^a-zA-Z\s]', '', text)   # Remove non-alphabetic characters
  text = re.sub(r'#', '', text)  # Remove hashtags
  text = text.lower() #lowercase

  tokens = word_tokenize(text)
  stopword = set(stopwords.words('english'))
  tokens = [word for word in tokens if word not in  stopword]
  lem = WordNetLemmatizer()
  token = [lem.lemmatize(i,wordnet.VERB) for i in tokens]
  return " ".join(token)

In [35]:
df['review'] = df['review'].apply(clean_sent)

In [38]:
df['review'].head()

0    one reviewers mention watch oz episode youll h...
1    wonderful little production film technique una...
2    think wonderful way spend time hot summer week...
3    basically theres family little boy jake think ...
4    petter matteis love time money visually stun f...
Name: review, dtype: object

In [39]:
tweet = "@user OMG!! This is soooo amazingggg 😍 #Excited http://example.com"
clean_tweet = clean_sent(tweet)
print(clean_tweet)

omg soooo amazingggg excite


In [40]:
df['sentiment'] = df['sentiment'].map({'positive':1,'negative':0})

In [42]:
df.head()

review  sentiment
0  one reviewers mention watch oz episode youll h...          1
1  wonderful little production film technique una...          1
2  think wonderful way spend time hot summer week...          1
3  basically theres family little boy jake think ...          0
4  petter matteis love time money visually stun f...          1

#BOW

In [43]:
from sklearn.feature_extraction.text import CountVectorizer

In [44]:
cv = CountVectorizer()
bow = cv.fit_transform(df['review'])

In [46]:
print(cv.vocabulary_)

{'one': 125916, 'reviewers': 147328, 'mention': 110655, 'watch': 192607, 'oz': 129368, 'episode': 55398, 'youll': 200195, 'hook': 82610, 'right': 148016, 'exactly': 57234, 'happen': 77046, 'methe': 111227, 'first': 63802, 'thing': 177251, 'strike': 169262, 'brutality': 23023, 'unflinching': 186273, 'scenes': 153119, 'violence': 190554, 'set': 157207, 'word': 197481, 'go': 71815, 'trust': 183354, 'show': 159421, 'faint': 59513, 'hearted': 78575, 'timid': 179593, 'pull': 141011, 'punch': 141096, 'regard': 145137, 'drug': 50089, 'sex': 157460, 'hardcore': 77340, 'classic': 31679, 'use': 188164, 'wordit': 197499, 'call': 24998, 'nickname': 120784, 'give': 71412, 'oswald': 127705, 'maximum': 108736, 'security': 155170, 'state': 167195, 'penitentary': 132007, 'focus': 65023, 'mainly': 105877, 'emerald': 53514, 'city': 31408, 'experimental': 58231, 'section': 155140, 'prison': 139096, 'cells': 27838, 'glass': 71527, 'front': 67545, 'face': 59124, 'inwards': 89559, 'privacy': 139154, 'high': 8

In [47]:
len(set(cv.vocabulary_))

201414

In [48]:
print((bow[0]).toarray())

[[0 0 0 ... 0 0 0]]


#N_grams

In [49]:
cv = CountVectorizer(ngram_range=(4,4))

#TF-IDF

In [50]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [51]:
tfidf = TfidfVectorizer()
tf = tfidf.fit_transform(df['review'])

In [52]:
print(tf[0].toarray())

[[0. 0. 0. ... 0. 0. 0.]]


In [54]:
df

review  sentiment
0      one reviewers mention watch oz episode youll h...          1
1      wonderful little production film technique una...          1
2      think wonderful way spend time hot summer week...          1
3      basically theres family little boy jake think ...          0
4      petter matteis love time money visually stun f...          1
...                                                  ...        ...
49995  think movie right good job wasnt creative orig...          1
49996  bad plot bad dialogue bad act idiotic direct a...          0
49997  catholic teach parochial elementary school nun...          0
49998  im go disagree previous comment side maltin on...          0
49999  one expect star trek movies high art fan expec...          0

[50000 rows x 2 columns]

#WORD2VEC

In [ ]:
!pip install gensim

In [ ]:
import kagglehub

# Download latest version
path = kagglehub.dataset_download("khulasasndh/game-of-thrones-books")

print("Path to dataset files:", path)

Path to dataset files: /root/.cache/kagglehub/datasets/khulasasndh/game-of-thrones-books/versions/1


In [ ]:
import nltk
nltk.download('punkt_tab')

from nltk import sent_tokenize
from gensim.utils import simple_preprocess

data = path
story = []
for filename in os.listdir(data):

    # Open the file with the correct encoding
    with open(os.path.join(data,filename), encoding='cp1252') as f:  # Try 'cp1252' or 'latin-1'
        corpus = f.read()
    raw_sent = sent_tokenize(corpus)
    for sent in raw_sent:
        story.append(simple_preprocess(sent))

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


In [ ]:
story

[['george',
  'martin',
  'dance',
  'with',
  'dragons',
  'book',
  'five',
  'of',
  'song',
  'of',
  'ice',
  'and',
  'fire',
  'dedication',
  'this',
  'one',
  'is',
  'for',
  'my',
  'fans',
  'for',
  'lodey',
  'trebla',
  'stego',
  'pod',
  'caress',
  'yags',
  'ray',
  'and',
  'mr',
  'kate',
  'chataya',
  'mormont',
  'mich',
  'jamie',
  'vanessa',
  'ro',
  'for',
  'stubby',
  'louise',
  'agravaine',
  'wert',
  'malt',
  'jo',
  'mouse',
  'telisiane',
  'blackfyre',
  'bronn',
  'stone',
  'coyote',
  'daughter',
  'and',
  'the',
  'rest',
  'of',
  'the',
  'madmen',
  'and',
  'wild',
  'women',
  'of',
  'the',
  'brotherhood',
  'without',
  'banners',
  'for',
  'my',
  'website',
  'wizards',
  'elio',
  'and',
  'linda',
  'lords',
  'of',
  'westeros',
  'winter',
  'and',
  'fabio',
  'of',
  'wic',
  'and',
  'gibbs',
  'of',
  'dragonstone',
  'who',
  'started',
  'it',
  'all',
  'for',
  'men',
  'and',
  'women',
  'of',
  'asshai',
  'in',
  '

In [ ]:
from gensim.models import Word2Vec

In [ ]:
model = Word2Vec(window=10,min_count=2)

In [ ]:
model.build_vocab(story)

In [ ]:
model.train(story, total_examples=model.corpus_count, epochs=model.epochs)

(6570433, 8628190)

In [ ]:
model.wv.most_similar('daenerys')

[('stormborn', 0.7642915844917297),
 ('queen', 0.7408725023269653),
 ('princess', 0.7387117147445679),
 ('targaryen', 0.731820285320282),
 ('myrcella', 0.7040486335754395),
 ('unburnt', 0.6944082379341125),
 ('joffrey', 0.6705151200294495),
 ('viserys', 0.6612463593482971),
 ('dorne', 0.6563417315483093),
 ('cersei', 0.6435917615890503)]